In [16]:
import requests
import time 

import pandas as pd
import numpy as np
from datetime import datetime

import os
import pathlib
import sys
import logging
import io

from portfolio_analytics import ForwardFillImputer, BackwardFillImputer

logging.basicConfig(filename='logs.log', level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)


import boto3

import  matplotlib.pyplot as plt

# Инициализируем подключение к ОХ
s3 = boto3.client('s3')
pd.set_option('display.max_rows', 50)

In [17]:
body = s3.get_object(Bucket='portfoliodata', Key='prepared_data/test.csv')['Body'].read()

stocks_df = pd.read_csv(io.BytesIO(body))
stocks_df.head()

begin    YRSB    ROSN    MTSS    RTKM    TATN  WTCMP   OGKB    SNGS  \
0  2008-01-09     NaN  227.74  374.75  291.87  154.60    NaN  3.640  30.501   
1  2008-01-10  19.200  230.60  373.88  292.00  153.50    7.0  3.527  30.430   
2  2008-01-11  19.200  223.38  374.95  295.50  154.22    NaN  3.544  30.400   
3  2008-01-14  19.050  224.00  379.80  299.00  158.50    7.0  3.560  30.692   
4  2008-01-15  20.882  221.98  374.90  301.49  157.44    6.9  3.550  30.400   

     UTAR  ...  SBERP   NLMK  MGTSP   RZSB   RTSB    APTK     VSMO  VRSBP  \
0  17.950  ...  69.62  104.6  793.1  1.849  0.378  1779.0  7610.00   4.50   
1  18.230  ...  70.00  105.0  793.0  1.726  0.379  1795.0  7681.00   4.40   
2  18.644  ...  70.30  105.0  770.0  1.722  0.378  1770.0  7635.00   4.45   
3  18.290  ...  70.41  104.0  773.0  1.720  0.380  1755.0  7600.00   4.10   
4  18.459  ...  71.00  104.0  780.0  1.670  0.377  1755.0  7635.06   4.20   

      PLZL   ASSB  
0  1153.00  0.600  
1  1207.00  0.649  
2  1208.00  0.649  
3  1254.00  0.660  
4  1277.78  0.655  

[5 rows x 31 columns]

In [18]:
stocks_df.shape

(4256, 31)

# Заполнение пропусков

In [19]:
stocks_df.isna().sum()

begin       0
YRSB     2147
ROSN        0
MTSS        9
RTKM       10
TATN        2
WTCMP    1477
OGKB        4
SNGS        0
UTAR       62
LPSB     2161
GMKN        4
DVEC       60
TASB     1080
KROT      421
LKOH        0
SBER        0
PMSB      692
LSNG       90
OMZZP     867
MVID       10
SBERP       0
NLMK        1
MGTSP     327
RZSB      946
RTSB     1034
APTK        4
VSMO        2
VRSBP    1913
PLZL        0
ASSB      910
dtype: int64

In [20]:
stocks_df = ForwardFillImputer().fit_transform(stocks_df)
stocks_df = BackwardFillImputer().fit_transform(stocks_df)

stocks_df.isna().sum().sum()

np.int64(0)

# Доходности

In [26]:
stocks_df.index = stocks_df.begin
stocks_df = stocks_df.drop(columns='begin')
stocks_df.head()

YRSB    ROSN    MTSS    RTKM    TATN  WTCMP   OGKB    SNGS  \
begin                                                                      
2008-01-09  19.200  227.74  374.75  291.87  154.60    7.0  3.640  30.501   
2008-01-10  19.200  230.60  373.88  292.00  153.50    7.0  3.527  30.430   
2008-01-11  19.200  223.38  374.95  295.50  154.22    7.0  3.544  30.400   
2008-01-14  19.050  224.00  379.80  299.00  158.50    7.0  3.560  30.692   
2008-01-15  20.882  221.98  374.90  301.49  157.44    6.9  3.550  30.400   

              UTAR   LPSB  ...  SBERP   NLMK  MGTSP   RZSB   RTSB    APTK  \
begin                      ...                                              
2008-01-09  17.950  5.352  ...  69.62  104.6  793.1  1.849  0.378  1779.0   
2008-01-10  18.230  5.400  ...  70.00  105.0  793.0  1.726  0.379  1795.0   
2008-01-11  18.644  5.550  ...  70.30  105.0  770.0  1.722  0.378  1770.0   
2008-01-14  18.290  5.450  ...  70.41  104.0  773.0  1.720  0.380  1755.0   
2008-01-15  18.459  5.420  ...  71.00  104.0  780.0  1.670  0.377  1755.0   

               VSMO  VRSBP     PLZL   ASSB  
begin                                       
2008-01-09  7610.00   4.50  1153.00  0.600  
2008-01-10  7681.00   4.40  1207.00  0.649  
2008-01-11  7635.00   4.45  1208.00  0.649  
2008-01-14  7600.00   4.10  1254.00  0.660  
2008-01-15  7635.06   4.20  1277.78  0.655  

[5 rows x 30 columns]

In [27]:

ratio = (stocks_df / stocks_df.shift(1)).where(stocks_df.shift(1) != 0, 1.0)
df_returns = np.log(ratio)

/Users/kekernikola/Desktop/Python projects/portfolio_management/.venv/lib/python3.9/site-packages/pandas/core/internals/blocks.py:393: RuntimeWarning: divide by zero encountered in log
  result = func(self.values, **kwargs)


In [28]:

window = 252  
cov_matrices_rolling = {}

for current_date in df_returns.index[window:]:
    window_slice = df_returns.loc[:current_date].tail(window)
    cov_mat = window_slice.cov()
    cov_matrices_rolling[current_date] = cov_mat


/Users/kekernikola/Desktop/Python projects/portfolio_management/.venv/lib/python3.9/site-packages/numpy/lib/_function_base_impl.py:2767: RuntimeWarning: invalid value encountered in subtract
  X -= avg[:, None]


In [29]:
cov_matrices_rolling

{'2009-01-16':            YRSB      ROSN      MTSS      RTKM      TATN     WTCMP      OGKB  \
 YRSB   0.004231  0.001147  0.000698  0.000068  0.000958  0.000100  0.000950   
 ROSN   0.001147  0.003208  0.002045  0.000756  0.002512  0.000025  0.002076   
 MTSS   0.000698  0.002045  0.002289  0.000761  0.002036  0.000046  0.001716   
 RTKM   0.000068  0.000756  0.000761  0.001126  0.000814  0.000077  0.000514   
 TATN   0.000958  0.002512  0.002036  0.000814  0.003530  0.000145  0.002236   
 WTCMP  0.000100  0.000025  0.000046  0.000077  0.000145  0.002249  0.000059   
 OGKB   0.000950  0.002076  0.001716  0.000514  0.002236  0.000059  0.003723   
 SNGS   0.000974  0.002563  0.001890  0.000684  0.002235  0.000066  0.001982   
 UTAR   0.000405  0.000914  0.001004  0.000433  0.001100  0.000087  0.001445   
 LPSB   0.000091 -0.000034  0.000043 -0.000091  0.000137 -0.000100 -0.000583   
 GMKN   0.000862  0.002123  0.001740  0.000733  0.001770  0.000132  0.001310   
 DVEC   0.001170  0.002004